## Imports:

In [45]:
!pip install --upgrade pip setuptools wheel

  Using cached pip-25.3-py3-none-any.whl (1.8 MB)
  Using cached setuptools-80.9.0-py3-none-any.whl (1.2 MB)
  Using cached wheel-0.45.1-py3-none-any.whl (72 kB)
  Attempting uninstall: wheel
    Found existing installation: wheel 0.37.0
    Uninstalling wheel-0.37.0:
      Successfully uninstalled wheel-0.37.0
  Attempting uninstall: setuptools
    Found existing installation: setuptools 58.0.4
    Uninstalling setuptools-58.0.4:
      Successfully uninstalled setuptools-58.0.4
  Attempting uninstall: pip
    Found existing installation: pip 21.2.4
    Uninstalling pip-21.2.4:
      Successfully uninstalled pip-21.2.4
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
spyder 5.1.5 requires pyqt5<5.13, which is not installed.
spyder 5.1.5 requires pyqtwebengine<5.13, which is not installed.
conda-repo-cli 1.0.4 requires pathlib, which is not installed.
anaconda-pr

In [46]:
!pip install langchain_core langchain_community langchain_ollama langchain_groq groq pymupdf faiss-cpu==1.12.0

  Using cached faiss_cpu-1.12.0-cp39-cp39-macosx_13_0_x86_64.whl.metadata (5.1 kB)
Using cached faiss_cpu-1.12.0-cp39-cp39-macosx_13_0_x86_64.whl (8.0 MB)
ERROR: Exception:
Traceback (most recent call last):
  File "/Users/neetikasaxena/opt/anaconda3/lib/python3.9/site-packages/pip/_internal/cli/base_command.py", line 107, in _run_wrapper
    status = _inner_run()
  File "/Users/neetikasaxena/opt/anaconda3/lib/python3.9/site-packages/pip/_internal/cli/base_command.py", line 98, in _inner_run
    return self.run(options, args)
  File "/Users/neetikasaxena/opt/anaconda3/lib/python3.9/site-packages/pip/_internal/cli/req_command.py", line 85, in wrapper
    return func(self, options, args)
  File "/Users/neetikasaxena/opt/anaconda3/lib/python3.9/site-packages/pip/_internal/commands/install.py", line 484, in run
    installed_versions[distribution.canonical_name] = distribution.version
  File "/Users/neetikasaxena/opt/anaconda3/lib/python3.9/site-packages/pip/_internal/metadata/pkg_resource

In [47]:
# env:
import os
from dotenv import load_dotenv
load_dotenv()
# Chat:
from operator import itemgetter
from langchain_core.documents import Document
from langchain_core.messages import AIMessage, HumanMessage, SystemMessage
from langchain_core.prompts import ChatPromptTemplate, MessagesPlaceholder
from langchain_core.output_parsers import StrOutputParser
# History
from langchain_core.chat_history import BaseChatMessageHistory
from langchain_community.chat_message_histories import ChatMessageHistory
from langchain_core.messages import trim_messages
from langchain_core.runnables import RunnableWithMessageHistory, RunnablePassthrough
# Load
from langchain_community.document_loaders import PyMuPDFLoader
from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain.chains.combine_documents import create_stuff_documents_chain
# Store
from langchain_ollama import OllamaEmbeddings
from langchain_community.vectorstores import FAISS
# Retrieve
from langchain.chains import create_retrieval_chain, create_history_aware_retriever

In [13]:
from IPython.display import Markdown
# from llm import get_response_stream, get_response

In [ ]:
# for chunk in get_response("hello", dummy=True):
#     print(chunk, end="", flush=True)

## LLM:

In [14]:
MAX_TOKENS = 16000
PER_DOC_TOKENS = 750
SYS_PROMPT_SIZE = 1000 # assumed
TOTAL_DOC_SIZE = 3000
DOC_COUNT = TOTAL_DOC_SIZE // PER_DOC_TOKENS

### Ollama - Gemma3:4b:

In [15]:
from langchain_ollama import ChatOllama

# Gemma3 context size -> 128K (1,31,072)
# 30k -> 91% RAM, 91% GPU
# 25k -> 82% RAM, 89% GPU
# 15k -> 66% RAM, 87% GPU


llm = ChatOllama(
    model="gemma3:latest", temperature=1,
    # model="gemma3:1b", temperature=1,
    #  num_predict=MAX_OUTPUT_TOKENS,
    num_gpu=35, num_ctx=MAX_TOKENS
)
llm.invoke("Hii")

AIMessage(content="Hi there! How's your day going so far? 😊 \n\nIs there anything you'd like to chat about, or were you just saying hello?", additional_kwargs={}, response_metadata={'model': 'gemma3:latest', 'created_at': '2025-11-25T18:59:17.333823Z', 'done': True, 'done_reason': 'stop', 'total_duration': 5791387667, 'load_duration': 3908150709, 'prompt_eval_count': 11, 'prompt_eval_duration': 931925916, 'eval_count': 34, 'eval_duration': 901088459, 'logprobs': None, 'model_name': 'gemma3:latest'}, id='run--bb256a1d-1986-4d2f-b866-b8beeb78e3ee-0', usage_metadata={'input_tokens': 11, 'output_tokens': 34, 'total_tokens': 45})

### Groq - Llama3:70B:

In [21]:
!pip install groq

In [23]:
# from langchain_groq import ChatGroq
# llm = ChatGroq(
#     model="llama-3.3-70b-versatile", temperature="1",
#     max_tokens=MAX_TOKENS, api_key=os.environ.get("GROQ_API_KEY"),
# )
# llm.invoke('hi')

In [ ]:
# Markdown(llm.invoke("write a story").content)

## Template:

<div class="alert alert-info">
    <strong>Limitations:</strong> Listed are some base assumptions in certain components of langchain components.
</div>

- `CreateHistoryAwareRetriever` assumes the latest-user-message key to be `input`
- `Trimmer` assumes the `ChatHistory` key to be `messages`
- `CreateStuffDocumentChain` assumes returns the clubbed `docs` in key `context`
- To overcome this, you need to use `RunnablePassthrough` or RunnableMap and assign those keys and variables accordingly.
- But remember, you need to manually set such things for all the variables which u are using different than default.

- So it's always good to follow the default keys and avoid complexity in chains.

### Chat:

In [24]:
template_chat = ChatPromptTemplate.from_messages(
    messages=[
        ("system",  "".join([
            "You are a highly knowledgeable and helpful AI assistant.\n"
            "You are provided with the user's chat history and external documents to assist in your response.\n\n"
            "Your task is to:\n"
            "- Accurately and clearly answer the user's latest question.\n"
            "- Incorporate any relevant information from the context documents enclosed below.\n"
            # "- Reference the source(s) whenever applicable.\n"
            "- Use appropriate markdown formatting for clarity and readability (e.g., bullet points, headings, code blocks, tables).\n\n"
            "- If not available in the context, mention that and then answer from your own knowledge.\n"
            "Contextual Documents:\n"
            "<CONTEXT>{context}</CONTEXT>"
        ])),
        MessagesPlaceholder(variable_name="chat_history"),
        ("human", "{input} \n\n **Strictly stick to the instructions!**")
    ]
)
template_chat

ChatPromptTemplate(input_variables=['chat_history', 'context', 'input'], input_types={'chat_history': list[typing.Annotated[typing.Union[typing.Annotated[langchain_core.messages.ai.AIMessage, Tag(tag='ai')], typing.Annotated[langchain_core.messages.human.HumanMessage, Tag(tag='human')], typing.Annotated[langchain_core.messages.chat.ChatMessage, Tag(tag='chat')], typing.Annotated[langchain_core.messages.system.SystemMessage, Tag(tag='system')], typing.Annotated[langchain_core.messages.function.FunctionMessage, Tag(tag='function')], typing.Annotated[langchain_core.messages.tool.ToolMessage, Tag(tag='tool')], typing.Annotated[langchain_core.messages.ai.AIMessageChunk, Tag(tag='AIMessageChunk')], typing.Annotated[langchain_core.messages.human.HumanMessageChunk, Tag(tag='HumanMessageChunk')], typing.Annotated[langchain_core.messages.chat.ChatMessageChunk, Tag(tag='ChatMessageChunk')], typing.Annotated[langchain_core.messages.system.SystemMessageChunk, Tag(tag='SystemMessageChunk')], typing.

In [ ]:
# Calculate tokens in this System message and pass rest of the max possible chat history:
# trim_keep = model_context - template_tokens - 250 (safe side)
# template_chat.messages[0].content

### Summarize:

In [55]:
template_summarize = ChatPromptTemplate.from_messages(
    messages=[
        ("system", "".join([
            "You are an expert at summarizing conversations into standalone prompts.\n"
            "You are given a complete chat history, ending with the user's latest message.\n\n"
            "Your task is to:\n"
            "- Understand the entire conversation context.\n"
            "- Identify references in the latest user message that relate to earlier messages.\n"
            "- Create a single clear, concise, and standalone question or prompt.\n"
            "- This final prompt should be fully understandable without needing the prior conversation.\n"
            "- It will be used to retrieve the most relevant documents.\n\n"
            "Only return the rewritten standalone prompt. Do not add explanations or formatting."
        ])),
        MessagesPlaceholder(variable_name="chat_history"),
        ("human", "{input}. \n\n **Make one standalone prompt as asked!**")
    ]
)
template_summarize

ChatPromptTemplate(input_variables=['chat_history', 'input'], input_types={'chat_history': list[typing.Annotated[typing.Union[typing.Annotated[langchain_core.messages.ai.AIMessage, Tag(tag='ai')], typing.Annotated[langchain_core.messages.human.HumanMessage, Tag(tag='human')], typing.Annotated[langchain_core.messages.chat.ChatMessage, Tag(tag='chat')], typing.Annotated[langchain_core.messages.system.SystemMessage, Tag(tag='system')], typing.Annotated[langchain_core.messages.function.FunctionMessage, Tag(tag='function')], typing.Annotated[langchain_core.messages.tool.ToolMessage, Tag(tag='tool')], typing.Annotated[langchain_core.messages.ai.AIMessageChunk, Tag(tag='AIMessageChunk')], typing.Annotated[langchain_core.messages.human.HumanMessageChunk, Tag(tag='HumanMessageChunk')], typing.Annotated[langchain_core.messages.chat.ChatMessageChunk, Tag(tag='ChatMessageChunk')], typing.Annotated[langchain_core.messages.system.SystemMessageChunk, Tag(tag='SystemMessageChunk')], typing.Annotated[l

In [ ]:
# Calculate tokens in this System message and pass rest of the max possible chat history:
# trim_keep = model_context - template_tokens - (1000tok/doc * n-docs) - 250 (safe side)
# template_summarize.messages

## Chat Message History:

In [26]:
chat_histories = {}

In [27]:
def get_session_history(session_id:str) -> BaseChatMessageHistory:
    # print("*"*40, session_id, "*"*40)
    if session_id not in chat_histories:
        chat_histories[session_id] = ChatMessageHistory()
        # log here for creation of new chat history
        print(f"Created chat hist for session id: `{session_id}`")    
    return chat_histories[session_id]

get_session_history("abv")

Created chat hist for session id: `abv`


InMemoryChatMessageHistory(messages=[])

In [28]:
get_session_history("abv")

InMemoryChatMessageHistory(messages=[])

### Trimmer:
- Due to some un-known issue in variable name of messages being "chat_history" or "messages" the trimmer cant be used in this RAG implementation.
- Reason: Trimmer expects "messages"
- But, if i use "messages", then idk why, the summarizer step does not call LLM at all, it just does not work, and is completely untraceable.
- Still, if u want to implement, use one runnable_passthrough before the trimmer in chain to convert chat_history > messages and the after its response, output > chat_history again! 

In [30]:
# # For summary 15k chat + 1k system and all
trim_summary = trim_messages(
    max_tokens=MAX_TOKENS - SYS_PROMPT_SIZE,
    strategy="last", token_counter=llm, start_on="human",
    allow_partial=True,  # include_system=True,
)

# # For chat 10k chat + 5*1k docs + 1k system and all
trim_chat = trim_messages(
    max_tokens=MAX_TOKENS - (TOTAL_DOC_SIZE) - SYS_PROMPT_SIZE,
    strategy="last", token_counter=llm, start_on="human",
    allow_partial=True,  # include_system=True,
)

## VectorStore:
### Embeddings:
- Notice that the embeddings are not offloaded at all to the GPU
- This is done because the Ollama repeatedly keeps loading and un-loading the emb / llm in each call.
- Even when I have memory, IDK why ollama loads only one of them?

In [31]:
embeddings = OllamaEmbeddings(model="mxbai-embed-large:latest", num_gpu=0)
embeddings

OllamaEmbeddings(model='mxbai-embed-large:latest', validate_model_on_init=False, base_url=None, client_kwargs={}, async_client_kwargs={}, sync_client_kwargs={}, mirostat=None, mirostat_eta=None, mirostat_tau=None, num_ctx=None, num_gpu=0, keep_alive=None, num_thread=None, repeat_last_n=None, repeat_penalty=None, temperature=None, stop=None, tfs_z=None, top_k=None, top_p=None)

### Loader:

In [32]:
!pwd

/Users/neetikasaxena/Documents/sanchit/sample_code/rag-with-gemma3/server


In [38]:
# file = PyMuPDFLoader(file_path="../assets/pdf_w_text.pdf", extract_tables='markdown', extract_images=True).load()
# file = PyMuPDFLoader(file_path="/Users/neetikasaxena/Documents/sanchit/sample_code/rag-with-gemma3/test_data/form_1095_C.pdf", 
#                      extract_tables='markdown', extract_images=True).load()

file = PyMuPDFLoader(file_path="/Users/neetikasaxena/Documents/sanchit/sample_code/rag-with-gemma3/test_data/candy_snacks.pdf", 
                     extract_tables='markdown', extract_images=True).load()



file

[Document(metadata={'producer': 'macOS Version 14.4.1 (Build 23E224) Quartz PDFContext', 'creator': '', 'creationdate': "D:20240409154109Z00'00'", 'source': '/Users/neetikasaxena/Documents/sanchit/sample_code/rag-with-gemma3/test_data/candy_snacks.pdf', 'file_path': '/Users/neetikasaxena/Documents/sanchit/sample_code/rag-with-gemma3/test_data/candy_snacks.pdf', 'total_pages': 26, 'format': 'PDF 1.4', 'title': '', 'author': '', 'subject': '', 'keywords': '', 'moddate': "D:20240409154109Z00'00'", 'trapped': '', 'modDate': "D:20240409154109Z00'00'", 'creationDate': "D:20240409154109Z00'00'", 'page': 0}, page_content="• Purpose\n• This content guide will help you create a best-in-class product page for your items. You'll learn how to build \nhigh-quality content and deliver a great member experience. Refer to this guide during the item setup process \nwhile completing the Item Setup Template.\n• This guide addresses the following content fields:\n•\nProduct Titles: Defines the specific ord

### Splitter:

In [39]:
splitter = RecursiveCharacterTextSplitter(
    chunk_size=PER_DOC_TOKENS, chunk_overlap=150,
)
splitter

### Database:

In [40]:
splitted = splitter.split_documents(file)
splitted

[Document(metadata={'producer': 'macOS Version 14.4.1 (Build 23E224) Quartz PDFContext', 'creator': '', 'creationdate': "D:20240409154109Z00'00'", 'source': '/Users/neetikasaxena/Documents/sanchit/sample_code/rag-with-gemma3/test_data/candy_snacks.pdf', 'file_path': '/Users/neetikasaxena/Documents/sanchit/sample_code/rag-with-gemma3/test_data/candy_snacks.pdf', 'total_pages': 26, 'format': 'PDF 1.4', 'title': '', 'author': '', 'subject': '', 'keywords': '', 'moddate': "D:20240409154109Z00'00'", 'trapped': '', 'modDate': "D:20240409154109Z00'00'", 'creationDate': "D:20240409154109Z00'00'", 'page': 0}, page_content="• Purpose\n• This content guide will help you create a best-in-class product page for your items. You'll learn how to build \nhigh-quality content and deliver a great member experience. Refer to this guide during the item setup process \nwhile completing the Item Setup Template.\n• This guide addresses the following content fields:\n•\nProduct Titles: Defines the specific ord

In [48]:
# This initialization needs 4 param, so rather moving to adding one doc manually.
database = FAISS.from_documents(documents=splitted, embedding=embeddings)
database

In [51]:
print(repr(splitted[0].page_content))
print(len(splitted[0].page_content.split(" ")))

"• Purpose\n• This content guide will help you create a best-in-class product page for your items. You'll learn how to build \nhigh-quality content and deliver a great member experience. Refer to this guide during the item setup process \nwhile completing the Item Setup Template.\n• This guide addresses the following content fields:\n•\nProduct Titles: Defines the specific order and structure your product title should follow in accordance with \ncopy description guidelines.\n•\nProduct Details: Specifies all required and recommended site attributes that contribute to content quality.\n•\nImages: Provides examples of expected images based on product type.\n• Use this guide before content creation and during item setup to answer any content-related needs."
106


### Retriever:

- So for 750 chars, there are appx 95 word (max 150)
- In order to retrieve the 3k tokens, we need to have 3k/150 = 20 chunks
- So, set k=20

In [52]:
retriever = database.as_retriever(
    search_type="similarity",
    search_kwargs={'k': 20}
)
retriever

VectorStoreRetriever(tags=['FAISS', 'OllamaEmbeddings'], vectorstore=<langchain_community.vectorstores.faiss.FAISS object at 0x7f84c10ec130>, search_kwargs={'k': 20})

In [53]:
retriever.invoke("what is the unit of measure?")

[Document(id='7d4c070a-b87b-4fae-b38a-267683d4ef84', metadata={'producer': 'macOS Version 14.4.1 (Build 23E224) Quartz PDFContext', 'creator': '', 'creationdate': "D:20240409154109Z00'00'", 'source': '/Users/neetikasaxena/Documents/sanchit/sample_code/rag-with-gemma3/test_data/candy_snacks.pdf', 'file_path': '/Users/neetikasaxena/Documents/sanchit/sample_code/rag-with-gemma3/test_data/candy_snacks.pdf', 'total_pages': 26, 'format': 'PDF 1.4', 'title': '', 'author': '', 'subject': '', 'keywords': '', 'moddate': "D:20240409154109Z00'00'", 'trapped': '', 'modDate': "D:20240409154109Z00'00'", 'creationDate': "D:20240409154109Z00'00'", 'page': 3}, page_content='PRODUCT TITLE / PRODUCT DESCRIPTION \nGuidelines\nUnit of Measure is always -  \n•\nIn lowercase\n•\nIn parentheses\n•\nSeparated by comma, no slash\n•\nExample : belVita Bites Breakfast Biscuits Variety Pack (1 oz., 36 \npk.)\nTotal weight of the sellable unit is not included in the Product Title \nif the component count is listed. 

## Summarizer:

- Old method.
- This is too much hard-coded, switch to the retrieval method with the create_stuff_chain to ingest the documents and get the answer in one single chain call.

In [ ]:
# chain = (
#     RunnablePassthrough().assign(messages=itemgetter("messages") | trim_chat)
#     | template_summarize | llm | StrOutputParser())

# summarizer_llm = RunnableWithMessageHistory(
#     runnable=chain,
#     get_session_history=get_session_history,
#     input_messages_key="input",
#     history_messages_key="messages",
# )

In [ ]:
# chat_histories[10] = ChatMessageHistory()
# chat_histories[10].messages = [
#     HumanMessage("Hello, I'm Bhushan, What is your name?"),
#     AIMessage("I am an AI assistant. I am not a human like you."),
#     HumanMessage("What is Artificial General Intelligence?"),
#     AIMessage("Artificial General Intelligence (AGI) refers to highly autonomous systems that outperform humans at most economically valuable work."),
# ]
# # )

In [ ]:
# summarizer_llm.invoke(
#     input={"input": "So it's not achieved yet?", },
#     config={"configurable": {"session_id": 10}}
# )

In [ ]:
# chat_histories[10].messages

## Runnable With History:
- Commented out as it's un-necessary and not used in the code.
- But, keep it, as it can be used in the future.

In [ ]:
# chain = (
#     RunnablePassthrough(name="Trim Chat History").assign(messages=itemgetter("messages") | trim_chat)
#     | template_chat | llm | StrOutputParser())

# chat_llm = RunnableWithMessageHistory(
#     runnable=chain,
#     get_session_history=get_session_history,
#     input_messages_key="input",
#     history_messages_key="messages",
# )

In [ ]:
# chat_llm.invoke(
#     input={
#         "input": "Hello, I'm Bhushan, What is your name?",
#         "context": "This is some random document which contains some random information."
#     },
#     config={
#         "configurable": {
#             "session_id": 15
#         }
#     }
# )

In [ ]:
# chat_llm.invoke(
#     input={
#         "input": "What did we discuss?",
#         "context": "There is no context available for this question."
#     },
#     config={
#         "configurable": {
#             "session_id": 15
#         }
#     }
# )

- If () add option to paste link and scrap whole content from there.

## Chain:

In [ ]:
# Make a passthrough which prints variables and passes them to next step
# def print_and_pass(input):
#     print(input)
#     return input

In [56]:
# 3 User Input + Chat History > Summarizer Template > Standalone Que > Get Docs
summarize_chain = create_history_aware_retriever(llm, retriever, template_summarize)
# summarize_chain = trim_summary | create_history_aware_retriever(llm, retriever, template_summarize)

# 4 Multiple Docs > Combine All > Chat Template > Final Output
qa_chain = create_stuff_documents_chain(llm=llm, prompt=template_chat)

# 2 Input + Chat History > [ `Summarizer Template` > `Get Docs` ] > [ `Combine` > `Chat Template` ] > Output
rag_chain = create_retrieval_chain(summarize_chain , qa_chain)

# 1 Final main chain:
conversational_rag_chain = RunnableWithMessageHistory(
    runnable=rag_chain,
    get_session_history=get_session_history,
    input_messages_key="input",
    history_messages_key="chat_history",
    output_messages_key="answer",
)
conversational_rag_chain

RunnableWithMessageHistory(bound=RunnableBinding(bound=RunnableBinding(bound=RunnableAssign(mapper={
  chat_history: RunnableBinding(bound=RunnableLambda(_enter_history), kwargs={}, config={'run_name': 'load_history'}, config_factories=[])
}), kwargs={}, config={'run_name': 'insert_history'}, config_factories=[])
| RunnableBinding(bound=RunnableLambda(_call_runnable_sync), kwargs={}, config={'run_name': 'check_sync_or_async'}, config_factories=[]), kwargs={}, config={'run_name': 'RunnableWithMessageHistory'}, config_factories=[]), kwargs={}, config={}, config_factories=[], get_session_history=<function get_session_history at 0x7f84c0d155e0>, input_messages_key='input', output_messages_key='answer', history_messages_key='chat_history', history_factory_config=[ConfigurableFieldSpec(id='session_id', annotation=<class 'str'>, name='Session ID', description='Unique identifier for a session.', default='', is_shared=True, dependencies=None)])

## Test:

### Database:

In [57]:
database.add_documents(
    [
        Document("Cats and Dogs are both popular pets."),
        Document("Cats are independent and low-maintenance pets."),
        Document("Dogs are loyal and require more attention."),
        Document("Cats are often seen as aloof and mysterious."),
        Document("Dogs are known for their loyalty and companionship."),
        Document("Cats are great for small living spaces."),
        Document("Cats are NOT AT ALL LOYAL."),
    ],
    embedding=embeddings
)

['0d0bb983-0436-4bc3-b1a9-90563eaf1760',
 '63ea4109-e11b-48eb-aac5-cf234a9c3d0e',
 '64ab81dd-caa4-4fc6-a802-f8caeb372863',
 '08214f30-26d1-4e5d-9a7a-73ab10d6b64e',
 '52b436ad-2894-4976-bddf-71e18d426228',
 '6764ac04-e32c-4353-b273-c896c1767b0c',
 'bcf19987-4aa1-44f7-a456-0d600f0b252d']

In [59]:
# database.search(search_type='similarity', query="what is the unit of measure?", k=8)
database.search(search_type='similarity', query="what are dogs known for ?", k=4)

[Document(id='52b436ad-2894-4976-bddf-71e18d426228', metadata={}, page_content='Dogs are known for their loyalty and companionship.'),
 Document(id='64ab81dd-caa4-4fc6-a802-f8caeb372863', metadata={}, page_content='Dogs are loyal and require more attention.'),
 Document(id='0d0bb983-0436-4bc3-b1a9-90563eaf1760', metadata={}, page_content='Cats and Dogs are both popular pets.'),
 Document(id='08214f30-26d1-4e5d-9a7a-73ab10d6b64e', metadata={}, page_content='Cats are often seen as aloof and mysterious.')]

### Summarize Chain:

In [121]:
summarize_chain.invoke(
    input={
        "input": "What animal was i talking about? Which one is most common apart from that animal?",
        "chat_history": [
            HumanMessage("Hello, I'm Bhushan, What is your name?"),
            AIMessage("I am an AI assistant. I am not a human like you."),
            HumanMessage("What are ur thoughts on Dogs?"),
            AIMessage("Dogs are loyal and require more attention."), 
        ]
    },
)

[Document(id='0d0bb983-0436-4bc3-b1a9-90563eaf1760', metadata={}, page_content='Cats and Dogs are both popular pets.'),
 Document(id='52b436ad-2894-4976-bddf-71e18d426228', metadata={}, page_content='Dogs are known for their loyalty and companionship.'),
 Document(id='64ab81dd-caa4-4fc6-a802-f8caeb372863', metadata={}, page_content='Dogs are loyal and require more attention.'),
 Document(id='75f46a43-e548-4f7a-a897-08578f626d0e', metadata={'session_id': 'user_3'}, page_content="Earth's atmosphere is composed primarily of nitrogen (about 78%) and oxygen (about 21%)."),
 Document(id='71667b85-67c7-4157-abad-62300dc83e2c', metadata={'session_id': 'user_3'}, page_content="Earth's atmosphere is composed primarily of nitrogen (about 78%) and oxygen (about 21%)."),
 Document(id='64a8822c-bb45-4da0-8ae3-cff5f251d1de', metadata={'session_id': 'public'}, page_content='Earth, Sun and Moon all three are part of the Solar System.'),
 Document(id='95c2747e-37a8-4161-afe3-4bcfde7b7bb7', metadata={'se

### QA - Chain:

In [61]:
qa_chain.invoke(
    input={
        "input": "Full form of RAG?",
        "context": [Document(page_content="This is some random document which contains some random information.")],
        "chat_history": [
            HumanMessage("hi"),
            AIMessage("hello"),
            HumanMessage("What is RAG?"),
            AIMessage("RAG is a technique to combine retrieval and generation."),
        ]
    },
    # config={"configurable": {"session_id": 15}}
)

'Retrieval-Augmented Generation.'

### RAG Chain:

In [62]:
rag_chain.invoke(
    input={
        "input": "Full form of RAG?",
        "context": [Document(page_content="This is some random document which contains some random information.")],
        "chat_history": [
            HumanMessage("hi"),
            AIMessage("hello"),
            HumanMessage("What is RAG?"),
            AIMessage("RAG is a technique to combine retrieval and generation."),
        ]
    },
    # config={"configurable": {"session_id": 15}}
)

{'input': 'Full form of RAG?',
 'context': [Document(id='fe52e86f-bb26-457d-a75d-c4b8d23d1d28', metadata={'producer': 'macOS Version 14.4.1 (Build 23E224) Quartz PDFContext', 'creator': '', 'creationdate': "D:20240409154109Z00'00'", 'source': '/Users/neetikasaxena/Documents/sanchit/sample_code/rag-with-gemma3/test_data/candy_snacks.pdf', 'file_path': '/Users/neetikasaxena/Documents/sanchit/sample_code/rag-with-gemma3/test_data/candy_snacks.pdf', 'total_pages': 26, 'format': 'PDF 1.4', 'title': '', 'author': '', 'subject': '', 'keywords': '', 'moddate': "D:20240409154109Z00'00'", 'trapped': '', 'modDate': "D:20240409154109Z00'00'", 'creationDate': "D:20240409154109Z00'00'", 'page': 5}, page_content="Highlights include the product's \nmost relevant information.\nWhat Highlights must have:\n•\n3-5 bullet point statements \n(maximum of 5)\n•\nLess than 65 characters per \nstatement\nWhat to avoid:\n•\nNO CAPS or periods\n•\nNo bolding or special \nformatting\n•\nDo not repeat item name\n•\

### Conv RAG:

In [63]:
conversational_rag_chain.invoke(
    input={"input":"Hello, I am Sanchit. What abt u?"},
    config={"configurable":{"session_id":120}}
)

Created chat hist for session id: `120`


{'input': 'Hello, I am Sanchit. What abt u?',
 'chat_history': [],
 'context': [Document(id='a2786271-e658-4868-9668-10145acfcabf', metadata={'producer': 'macOS Version 14.4.1 (Build 23E224) Quartz PDFContext', 'creator': '', 'creationdate': "D:20240409154109Z00'00'", 'source': '/Users/neetikasaxena/Documents/sanchit/sample_code/rag-with-gemma3/test_data/candy_snacks.pdf', 'file_path': '/Users/neetikasaxena/Documents/sanchit/sample_code/rag-with-gemma3/test_data/candy_snacks.pdf', 'total_pages': 26, 'format': 'PDF 1.4', 'title': '', 'author': '', 'subject': '', 'keywords': '', 'moddate': "D:20240409154109Z00'00'", 'trapped': '', 'modDate': "D:20240409154109Z00'00'", 'creationDate': "D:20240409154109Z00'00'", 'page': 18}, page_content='5. Nice to Have – Company Callouts / Product Usage / Lifestyle Graphics'),
  Document(id='2a09c111-c967-4426-87d3-585e68be874a', metadata={'producer': 'macOS Version 14.4.1 (Build 23E224) Quartz PDFContext', 'creator': '', 'creationdate': "D:2024040915410

In [64]:
conversational_rag_chain.invoke(
    input={"input":"What are popular pets?"},
    config={"configurable":{"session_id":120}}
)

{'input': 'What are popular pets?',
 'chat_history': [HumanMessage(content='Hello, I am Sanchit. What abt u?', additional_kwargs={}, response_metadata={}),
  AIMessage(content='Hello Sanchit, nice to meet you! I am a helpful AI assistant. I can answer your questions and provide information based on the documents I have been provided.', additional_kwargs={}, response_metadata={})],
 'context': [Document(id='0d0bb983-0436-4bc3-b1a9-90563eaf1760', metadata={}, page_content='Cats and Dogs are both popular pets.'),
  Document(id='52b436ad-2894-4976-bddf-71e18d426228', metadata={}, page_content='Dogs are known for their loyalty and companionship.'),
  Document(id='64ab81dd-caa4-4fc6-a802-f8caeb372863', metadata={}, page_content='Dogs are loyal and require more attention.'),
  Document(id='63ea4109-e11b-48eb-aac5-cf234a9c3d0e', metadata={}, page_content='Cats are independent and low-maintenance pets.'),
  Document(id='6764ac04-e32c-4353-b273-c896c1767b0c', metadata={}, page_content='Cats are 

In [65]:
conversational_rag_chain.invoke(
    input={"input":"Describe CATS?"},
    config={"configurable":{"session_id":120}}
)

{'input': 'Describe CATS?',
 'chat_history': [HumanMessage(content='Hello, I am Sanchit. What abt u?', additional_kwargs={}, response_metadata={}),
  AIMessage(content='Hello Sanchit, nice to meet you! I am a helpful AI assistant. I can answer your questions and provide information based on the documents I have been provided.', additional_kwargs={}, response_metadata={}),
  HumanMessage(content='What are popular pets?', additional_kwargs={}, response_metadata={}),
  AIMessage(content='Based on the provided documents, popular pets are Cats and Dogs.', additional_kwargs={}, response_metadata={})],
 'context': [Document(id='63ea4109-e11b-48eb-aac5-cf234a9c3d0e', metadata={}, page_content='Cats are independent and low-maintenance pets.'),
  Document(id='08214f30-26d1-4e5d-9a7a-73ab10d6b64e', metadata={}, page_content='Cats are often seen as aloof and mysterious.'),
  Document(id='6764ac04-e32c-4353-b273-c896c1767b0c', metadata={}, page_content='Cats are great for small living spaces.'),
  

In [66]:
conversational_rag_chain.invoke(
    input={"input":"1. Are they LOYAL? 2. What do I mean by THEY?"},
    config={"configurable":{"session_id":120}}
)

{'input': '1. Are they LOYAL? 2. What do I mean by THEY?',
 'chat_history': [HumanMessage(content='Hello, I am Sanchit. What abt u?', additional_kwargs={}, response_metadata={}),
  AIMessage(content='Hello Sanchit, nice to meet you! I am a helpful AI assistant. I can answer your questions and provide information based on the documents I have been provided.', additional_kwargs={}, response_metadata={}),
  HumanMessage(content='What are popular pets?', additional_kwargs={}, response_metadata={}),
  AIMessage(content='Based on the provided documents, popular pets are Cats and Dogs.', additional_kwargs={}, response_metadata={}),
  HumanMessage(content='Describe CATS?', additional_kwargs={}, response_metadata={}),
  AIMessage(content='Cats are independent and low-maintenance pets. Cats are often seen as aloof and mysterious. Cats are great for small living spaces. Cats and Dogs are both popular pets. Cats are NOT AT ALL LOYAL.', additional_kwargs={}, response_metadata={})],
 'context': [Doc

# Filter data by users:

## Add:

In [102]:
sun_docs = [
    Document(
        page_content="The Sun is a nearly perfect sphere of hot plasma, at the center of the Solar System.",
        metadata={"session_id": "user_1"}
    ), 
    Document(
        page_content="It is composed primarily of hydrogen (about 74%) and helium (about 24%) by mass.",
        metadata={"session_id": "user_1"}
    ),
    Document(
        page_content="The Sun's core temperature reaches approximately 15 million degrees Celsius.",
        metadata={"session_id": "user_1"}
    ),
    Document(
        page_content="Solar flares and sunspots are caused by magnetic field activity on the Sun's surface.",
        metadata={"session_id": "user_1"}
    ),
    Document(
        page_content="Light from the Sun takes about 8 minutes and 20 seconds to reach Earth.",
        metadata={"session_id": "user_1"}
    ),
   
]

In [103]:
moon_docs = [
    Document(
        page_content="The Moon is Earth's only natural satellite and the fifth largest moon in the Solar System.",
        metadata={"session_id": "user_2"}
    ),
    Document(
        page_content="It is about 1/6th the size of Earth and has a diameter of about 3,474 kilometers.",
        metadata={"session_id": "user_2"}
    ),
    Document(
        page_content="The Moon's surface is covered with craters, mountains, and flat plains called maria.",
        metadata={"session_id": "user_2"}
    ),
    Document(
        page_content="The Moon has no atmosphere, which means it cannot support life as we know it.",
        metadata={"session_id": "user_2"}
    ),
    Document(
        page_content="The Moon's gravitational pull affects Earth's tides.",
        metadata={"session_id": "user_2"}
    )
]

In [69]:
earth_docs = [
    Document(
        page_content="Earth is the third planet from the Sun and the only known planet to support life.",
        metadata={"session_id": "user_3"}
    ),
    Document(
        page_content="It has a diameter of about 12,742 kilometers and is composed of rock and metal.",
        metadata={"session_id": "user_3"}
    ),
    Document(
        page_content="Earth's atmosphere is composed primarily of nitrogen (about 78%) and oxygen (about 21%).",
        metadata={"session_id": "user_3"}
    ),
    Document(
        page_content="The Earth has one natural satellite, the Moon.",
        metadata={"session_id": "user_3"}
    ),
    Document(
        page_content="Earth's surface is covered by about 71% water.",
        metadata={"session_id": "user_3"}
    )
]

In [70]:
common_docs = [
    Document(
        page_content="Moon revolves around Earth, while Earth revolves around the Sun.",
        metadata={"session_id": "public"}
    ),
    Document(
        page_content="Earth, Sun and Moon all three are part of the Solar System.",
        metadata={"session_id": "public"}
    ),
]

## Embed:

In [107]:
user_1_docs = database.add_documents(sun_docs, embedding=embeddings)
user_2_docs = database.add_documents(moon_docs, embedding=embeddings)
user_3_docs = database.add_documents(earth_docs, embedding=embeddings)
public_docs = database.add_documents(common_docs, embedding=embeddings)
user_3_docs

['15b5166e-7dda-404c-8756-817652b7380d',
 '71e80cbf-2386-4337-98d6-1f9bc1246074',
 '71667b85-67c7-4157-abad-62300dc83e2c',
 'd7f937d7-b4bd-4e31-b065-9fb0d55e53e3',
 '047c0ece-de86-427b-841d-d8ef1505efc8']

## Retrieve with filters:
- https://python.langchain.com/docs/integrations/vectorstores/faiss/#query-directly

In [94]:
retriever = database.as_retriever(
    search_type="similarity_score_threshold",
    search_kwargs={'k': 4, 'score_threshold': 0.05}
)
retriever

VectorStoreRetriever(tags=['FAISS', 'OllamaEmbeddings'], vectorstore=<langchain_community.vectorstores.faiss.FAISS object at 0x7f84c10ec130>, search_type='similarity_score_threshold', search_kwargs={'k': 4, 'score_threshold': 0.05})

In [100]:
retriever.invoke("Does moon revolve around earth?", filter={"session_id": "user_1"})

[Document(id='3ee59c85-64dd-43fa-ac70-e065f9b1bf2d', metadata={'session_id': 'user_1'}, page_content="The Moon is Earth's only natural satellite and the fifth largest moon in the Solar System."),
 Document(id='cd51a6fb-ab0f-468a-a343-20a81b47af16', metadata={'session_id': 'user_1'}, page_content='Light from the Sun takes about 8 minutes and 20 seconds to reach Earth.'),
 Document(id='2542487c-a6b3-402f-9fb7-f1a4a59dad70', metadata={'session_id': 'user_1'}, page_content='The Sun is a nearly perfect sphere of hot plasma, at the center of the Solar System.'),
 Document(id='b75633fd-31ce-4b14-9e1a-7c05f2feffa2', metadata={'session_id': 'user_1'}, page_content='It is composed primarily of hydrogen (about 74%) and helium (about 24%) by mass.')]

In [110]:
retriever.invoke("which is earth's only natural sitelite ?", filter={"session_id": "user_2"})

[Document(id='44480fa4-596e-4978-9dc2-cd889aa0c3e9', metadata={'session_id': 'user_2'}, page_content="The Moon is Earth's only natural satellite and the fifth largest moon in the Solar System."),
 Document(id='8aa8194f-c301-4b92-bebc-a114815f9a93', metadata={'session_id': 'user_2'}, page_content="The Moon's surface is covered with craters, mountains, and flat plains called maria."),
 Document(id='cad1d41d-2eb7-49a0-afc9-d1d9e4f4d85f', metadata={'session_id': 'user_2'}, page_content='It is about 1/6th the size of Earth and has a diameter of about 3,474 kilometers.'),
 Document(id='774fe30c-762f-41a8-84f6-259ba0817454', metadata={'session_id': 'user_2'}, page_content='The Moon has no atmosphere, which means it cannot support life as we know it.')]

In [83]:
retriever.invoke("What is the Earth?", filter={"session_id": "user_3"})

[Document(id='53f8f17f-0354-4608-9741-c6c06c33b317', metadata={'session_id': 'user_3'}, page_content='Earth is the third planet from the Sun and the only known planet to support life.')]

## Delete:

In [106]:
database.delete(user_2_docs)

True

In [85]:
retriever.invoke("What is the Earth?", filter={"session_id": "user_3"})

No relevant docs were retrieved using the relevance score threshold 0.5


[]

## Multiple Conditional Filters:
- https://github.com/langchain-ai/langchain/discussions/20202

In [109]:
retriever.invoke(
    input="which is earth's only natural sitelite ?",
    filter={
        "$or": [
            {"session_id": "user_2"},
            {"session_id": "user_1"},
        ]
    })

[Document(id='44480fa4-596e-4978-9dc2-cd889aa0c3e9', metadata={'session_id': 'user_2'}, page_content="The Moon is Earth's only natural satellite and the fifth largest moon in the Solar System."),
 Document(id='e4b88b13-4f27-4eba-8f46-3223fd816885', metadata={'session_id': 'user_1'}, page_content='Light from the Sun takes about 8 minutes and 20 seconds to reach Earth.'),
 Document(id='8aa8194f-c301-4b92-bebc-a114815f9a93', metadata={'session_id': 'user_2'}, page_content="The Moon's surface is covered with craters, mountains, and flat plains called maria."),
 Document(id='cad1d41d-2eb7-49a0-afc9-d1d9e4f4d85f', metadata={'session_id': 'user_2'}, page_content='It is about 1/6th the size of Earth and has a diameter of about 3,474 kilometers.')]

> So basically:
- When user uploads something, assign it a id in metadata
- Save the ids of embedded docs user-wise in some database
- Use the filter to filter the docs by user-id + public docs
- Once done, use the list of ids from database to delete the user data
- Maybe using in memory SQLite would be best option

# Testing:
`Note:`
- In this file so far I used 'session_id' for metadata
- But, in project, it is 'user_id'

## Loading FAISS (disk) and checking all docs:

In [113]:
from langchain_community.vectorstores import FAISS
from langchain_ollama import OllamaEmbeddings
embeddings = OllamaEmbeddings(model="mxbai-embed-large:latest")

db = FAISS.load_local(
    folder_path="./user_faiss",
    index_name="index",
    embeddings=embeddings,
    allow_dangerous_deserialization=True
)

In [114]:
db.similarity_search(
    query="a",
    filter={
        "$or": [
            {"user_id": "nervous_nerd"},
            {"user_id": "public"}
        ]
    },
    kwargs={"k": 5}
)

[]

In [115]:
db.similarity_search(
    query="ballot",
    filter={"user_id": "nervous_nerd"}
    # kwargs={"k": 5, "score_threshold": 0}
)

[]

## Building As retriever with filters:
+ `Issue is that we are unable to set some filter while invoking RAG chain.`

- Tried, but failed:
    - https://github.com/langchain-ai/langchain/issues/9195#issuecomment-1810893811
- Working Solution:
    - https://github.com/langchain-ai/langchain/issues/9195#issuecomment-2095196865

In [117]:
from langchain_community.vectorstores import FAISS
from langchain_ollama import OllamaEmbeddings
embeddings = OllamaEmbeddings(model="mxbai-embed-large:latest")

db = FAISS.load_local(
    folder_path="./user_faiss",
    index_name="index",
    embeddings=embeddings,
    allow_dangerous_deserialization=True
)

retriever = db.as_retriever()

In [118]:
from langchain_core.runnables import ConfigurableField
configurable_retriever = retriever.configurable_fields(
    search_kwargs=ConfigurableField(
        id="search_kwargs",
        name="Search Kwargs",
        description="The search kwargs to use",
    )
)

In [119]:
config = {
    "configurable": {
        "search_kwargs": {
            "k": 5,
            "search_type": "similarity",
            # And here comes the hero:
            "filter": {
                "$or": [
                    {"user_id": "curious_cat"},
                    {"user_id": "public"}
                ]
            },
        }
    }
}

In [120]:
configurable_retriever.invoke(
    input="What is the Sun?",
    config=config
)

[]

<div class="alert alert-warning">
    <h1>Important:</h1> 
    <!-- <h1><strong>Important:</strong></h1>  -->
</div>

- Just figured this out
- if u are having LLM call in the chain, but still it is not working, the possible reason is `ChatPromptTemplate`.
- If history is empty, then Template is skipped
- And maybe hence, all further calls as well!!
- So, if LLM is not getting called, try passing some history manually

## My issue
- I was using "messages" for the chat history
- Cause, trimmer expects "messages" key for input
- But, somehow, prompt template was not able to use "messages" key even though it was set explicitly like that.
- Once replaced with "chat_history", it worked.
- Also, for output always use "answer" key (in create hist aware retriever in Conversational RAG)